# Cerebellar Mean Field model

Please cite: 
<b> A multi-layer mean-field model for the cerebellar cortex: design, validation, and prediction; </b>
Roberta M. Lorenzi, Alice Geminiani, Yann Zerlaut, Alain Destexhe, Claudia A.M. Gandini Wheeler-Kingshott, Fulvia Palesi, Claudia Casellato, Egidio D’Angelo;
bioRxiv 2022.11.24.517708; doi: https://doi.org/10.1101/2022.11.24.517708

<br>contact: robertamaria.lorenzi01@universitadipavia.it</br>

## What is the Mean Field?

Mean Field (MF) is an approximation technique that provides a statistical summary of a spiking neural network behaviour (SNN) (Boustani and Destexhe 2009). In practice, the activity of a complex SNN (many equations!!!) is summarized through the statistical moments of membrane voltage fluctuation (average μV, the standard deviation σV and the autocorrelation time 𝜏V).

The heuristic approach used here (Zerlaut et al., 2016; 2018) relies on Transfer Function (TF) that allows to transfer microscale propeties (single neuron) into mesoscale (MF granularity).

The fundamental step to write MF equations are:

- 1) Choose a single neuron model. Here Extended Generalized LIF (Geminiani et al. 2018, 2019)
- 2) Build up a network. Here we used BSB (De Schepper et al. 2022)
- 3) Fit the Transfer function (Zerlaut et al. 2016, 2018; Carlu et al.2020)

This Notebook simulates the cerebbellar MF activity build up as described in 1) to 3). The complete pipeline is described in Lorenzi et al. 2022 (https://doi.org/10.1101/2022.11.24.517708), a summary of the steps is reported below.



### Let's start!

### 1) Single neuron model Spiking Neural Network

E-GLIF is a point neuron model derived from the leaky-integrate-and-fire model family (LIF),
which computes the membrane potential dynamic with a set of three interconnected equations (section 3.3.1), explicitly accounting for the time evolution of
adaptation and depolarization currents.

\begin{equation}
\frac{dV_m}{dt} = \frac{1}{C_m}(\frac{Cm}{\tau_m}(V_m(t) - E_L) -I_a(t) + I_d(t) + I_e(t)+I_s)
\end{equation}

\begin{equation}
\frac{dI_a}{dt} = k_a(V_m(t) - E_L) - k_2 I_a(t)
\end{equation}

\begin{equation}
\frac{dI_d}{dt} = - k_1I_d(t)
\end{equation}

(Is = external stimulation current; Cm = membrane capacitance; τm = membrane time constant; EL = resting potential; Ie = endogenous current; ka, k2 = adaptation constants; k1 = Id decay rate)


When a spike occurs: V = V_reset ; Ia = Ia + A2 ; Idep = A1 (V_reset = reset value for the membrane voltage,A2, A1 = update constants)

### 2) Spiking Neural Network
SNN was built by interconnecting E-GLIF neurons with alpha synapses conductance and SNN activity was simulated using BSB interfaced with NEST

(Extra info: Geminiani et al.,2018 https://doi.org/10.3389/fninf.2018.00088 and Geminiani et al., 2019 https://doi.org/10.3389/fncom.2019.00035)

### 3) Transfer Funcrion Formalism (TF)

TFs are the core of this formalis, enabling us to translate single neuron properties to a mesoscale level by computing population-level conductances that in turns depend on the statistical moment of the membran potential fluctations

## Mean field model simulations
Second order MF for 4 cerebellar populations: GrC = Granule Cells, GoC = Golgi Cells, MLI = Molecular Layer Interneuron, PC = Purkinje Cells.

Here we tested cerebellar MF for cortical and sensory-like input:

In [ ]:
pip install plotly

In [1]:
#import the libraries
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import sys
sys.path.append('../')
from MF_prediction.load_config_TF import *
from MF_prediction.master_equation_CRBL_MF import *
from MF_prediction.theoretical_tools import *

In [2]:
Ngrc = 28615
Ngoc = 70
Nmossy = 2336
Nmli = 299+147
Npc = 99

In [3]:
dt = 1e-4
sim_len = 0.5

In [4]:
T = 3.5e-3
w = 0. #adaptation not included at the moment

In [5]:
root_path = 'coeffP/' #folder where P coefficients were stored

NRN1, NRN2, NRN3, NRN4 = 'GrC', 'GoC', 'MLI', 'PC'
NTWK = 'CRBL_CONFIG_20PARALLEL_wN'

FILE_GrC = root_path  + 'GrC_fit.npy'
FILE_GoC = root_path + 'GoC_fit.npy'
FILE_MLI = root_path + 'MLI_fit.npy'
FILE_PC = root_path + 'PC_fit.npy'

TFgrc = load_transfer_functions(NRN1, NTWK, FILE_GrC, alpha=2.0)
TFgoc = load_transfer_functions_goc(NRN2, NTWK, FILE_GoC, alpha=1.3)
TFmli = load_transfer_functions(NRN3, NTWK, FILE_MLI, alpha=5)
TFpc = load_transfer_functions(NRN4, NTWK, FILE_PC, alpha=5)


synaptic network_scaffold parameters in SI units [V, F, s]
..................... Loading TFs
Neuron and Network:  GrC CRBL_CONFIG_20PARALLEL_wN
Loaded P file:  coeffP/GrC_fit.npy


[-0.42576682  0.00690724  0.02267742  0.48195387  0.21620201]
synaptic network_scaffold parameters in SI units [V, F, s]
..................... Loading TFs
Neuron and Network:  GoC CRBL_CONFIG_20PARALLEL_wN
Loaded P file:  coeffP/GoC_fit.npy


synaptic network_scaffold parameters in SI units [V, F, s]
..................... Loading TFs
Neuron and Network:  MLI CRBL_CONFIG_20PARALLEL_wN
Loaded P file:  coeffP/MLI_fit.npy


[-0.12788359 -0.00122987  0.0121506  -0.09311194 -0.06318328]
synaptic network_scaffold parameters in SI units [V, F, s]
..................... Loading TFs
Neuron and Network:  PC CRBL_CONFIG_20PARALLEL_wN
Loaded P file:  coeffP/PC_fit.npy


[-0.07999933  0.008472    0.00423417  0.00622404  0.01376171]


In [6]:
t = np.arange(0, sim_len, dt)

In [7]:
def plot_MF_activity(t, X):
    fig = go.Figure()

    fig = make_subplots(rows=5, cols=1)

    fig.add_trace(go.Scatter(x=t, y=X[:,0],
                                 mode='lines',
                                 name='$\\nu_{GrC}$',
                                 line=dict(color = "red")),
                      row=4, col=1
                      )
    
    fig.add_trace(go.Scatter(x=t, y=X[:,1],
                                 mode='lines',
                                 name='$\\nu_{GoC}$',
                                 line=dict(color = "blue")),
                      row=3, col=1
                      )
        
    fig.add_trace(go.Scatter(x=t, y=X[:,9],
                                 mode='lines',
                                 name='$\\nu_{MLI}$',
                                 line=dict(color = "orange")),
                      row=2, col=1
                      )

    fig.add_trace(go.Scatter(x=t, y=X[:,10],
                                 mode='lines',
                                 name='$\\nu_{PC}$',
                                 line=dict(color = "green")),
                      row=1, col=1
                      )
    
    fig.add_trace(go.Scatter(x=t, y=X[:,8],
                                 mode='lines',
                                 name='$\\nu_{drive}$',
                                 line=dict(color = "orchid")),
                      row=5, col=1
                      )


    fig.update_xaxes(title_text="time [s]", row=1, col=1)
    fig.update_xaxes(title_text="time [s]", row=2, col=1)
    fig.update_xaxes(title_text="time [s]", row=3, col=1)
    fig.update_xaxes(title_text="time [s]", row=4, col=1)
    fig.update_xaxes(title_text="time [s]", row=5, col=1)


    # Update yaxis properties
    fig.update_yaxes(title_text="GrC activity [Hz]", row=4, col=1)
    fig.update_yaxes(title_text="GoC activity [Hz]", row=3, col=1)
    fig.update_yaxes(title_text="MLI activity [Hz]", row=2, col=1)
    fig.update_yaxes(title_text="PC activity [Hz]", row=1, col=1)
    fig.update_yaxes(title_text="Input from mossy [Hz]", row=5, col=1)


    # Update title
    fig.update_layout(title_text='Mean Field Prediction', height=900)
    fig.show()

<b> Cortical-like input </b> 

In [8]:
def rect_input(time, t_start, t_end, minval, freq, noise_freq):

    """
    time = time vector of simulation
    t_start = start of the step INDEX
    t_end = end of the step INDEX
    minval = baseline value (deviation from 0)
    freq = peak value
    noise_freq = random noise frequencies
    """

    y = np.ones(len(time)) * freq + np.random.rand(len(time)) * noise_freq
    y[:t_start] = y[:t_start]*0+np.random.rand(t_start)*noise_freq
    y[t_end:] = y[t_end:]*0+np.random.rand(len(time) - t_end)*noise_freq
    y = y + minval

    return y

In [9]:
f_backnoise = np.random.rand(len(t))*4 #background noise set around 4 Hz

amplitude =7.5
freq1 = 15
freq2 = 30
freq3 = 1
f_sin1 = amplitude * np.sin(2 * np.pi * freq1 * t) + amplitude
f_sin2 = amplitude * np.sin(2*np.pi*freq2*t)+ amplitude
f_sin3 = amplitude * np.sin(2 * np.pi * freq3 * t) + amplitude

fmulti_sin = f_sin1 + f_sin2 + f_sin3 
fmossy_cort = fmulti_sin + f_backnoise

In [10]:
# X = vector of activity with Vp = population p mean activity, Csp = covariance between population s and p

# X = [Vgrc, Vgoc, Cgrcgrc, Cgrcgoc, Cgrcm, Cmgoc, Cgocgoc, Cmm, Vm, Vmli, Vpc, Cmlimli, Cmlipc, Cgrcpc, Cgrcmli,
#     Cpcpc, Cmligoc, Cmlimossy, Cpcgoc, Cpcmossy]


CI_vec = [0.5, 5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, fmossy_cort[0], 15, 38, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]

X_cort = find_fixed_point_mossy(TFgrc, TFgoc, TFmli, TFpc, CI_vec, t, w, fmossy_cort,
                           Ngrc, Ngoc, Nmossy, Nmli, Npc, T, verbose=False)

In [11]:
plot_MF_activity(t, X_cort)

<b> Sensory-like stimulus </b>

In [12]:
f_tone = rect_input(time=t, t_start=1250, t_end=3750, minval=0, freq=50, noise_freq=0)
fmossy_sens = fmossy_cort + f_tone

In [13]:
# X = vector of activity with Vp = population p mean activity, Csp = covariance between population s and p

# X = [Vgrc, Vgoc, Cgrcgrc, Cgrcgoc, Cgrcm, Cmgoc, Cgocgoc, Cmm, Vm, Vmli, Vpc, Cmlimli, Cmlipc, Cgrcpc, Cgrcmli,
#     Cpcpc, Cmligoc, Cmlimossy, Cpcgoc, Cpcmossy]


CI_vec = [0.5, 5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, fmossy_sens[0], 15, 38, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5, 0.5]

X_sens = find_fixed_point_mossy(TFgrc, TFgoc, TFmli, TFpc, CI_vec, t, w, fmossy_sens,
                           Ngrc, Ngoc, Nmossy, Nmli, Npc, T, verbose=False)

In [14]:
plot_MF_activity(t, X_sens)

## References:

- Cerebellar MF model: Lorenzi et al. 2022 (https://doi.org/10.1101/2022.11.24.517708)
- E-GLIF: Geminiani et al. 2018, 2019 (https://doi.org/10.3389/fninf.2018.00088 and https://doi.org/10.3389/fncom.2019.00035)
- BSB: De Schepper et al. 2022 (https://doi.org/10.1038/s42003-022-04213-y)
- Mathematics: Boustani and Destexhe 2009 (https://doi.org/10.1162/neco.2009.02-08-710)
- TF formalism: Zerlaut et al. 2018 (https://doi.org/10.1007/s10827-017-0668-2)
- TF Fitting procedure: Zerlaut et al. 2016  (https://doi.org/10.1113/JP272317)
- MF with adaptation: Di Volo et al. 2019 (https://doi.org/10.1162/neco_a_01173)
- MF review for different neuron model: Carlu et al. 2020 (https://doi.org/10.1152/jn.00399.2019)